In [96]:
import requests
from urllib.parse import urlencode
from datetime import datetime

In [97]:
# This is function for getting lat, lng, address and place id
def getGeocode(coordinates, api_key):
	data = []
	for coordinate in coordinates:
		responses = requests.get(
				'https://maps.googleapis.com/maps/api/geocode/json?' + urlencode(
					{'address': coordinate, 'key': api_key, 'sensor': 'false'}
				)
			)
		
		resp = responses.json()

		if resp['status'] == 'OK':
			place_id = resp['results'][0]['place_id']
			data.append({
				'place_id': place_id
			})
		else:
			print('JSON Failed:', resp)
			data.append({
				'place_id': 'Place ID is not found'
			})
		
	return data

In [98]:
# This is function for storing review data in array
def getPlaceDetails(place_id, api_key):
	response = requests.get(
			'https://maps.googleapis.com/maps/api/place/details/json?' + urlencode(
				{'place_id': place_id, 'key': api_key, 'region': 'id', 'language': 'id', 'reviews_no_translations': 'true'}
			)
		)

	resp = response.json()

	if resp['status'] == 'OK':
		reviews = resp['result'].get('reviews', [])
		name = resp['result'].get('name', 'Name is not found')
		icon = resp['result'].get('icon', 'Icon is not found')
		icon_background_color = resp['result'].get('icon_background_color', 'Icon background color is not found')
		icon_mask_base_uri = resp['result'].get('icon_mask_base_uri', 'Icon mask base uri is not found')
		international_phone_number = resp['result'].get('international_phone_number', 'International phone number is not found')
		current_opening_hours = resp['result'].get('current_opening_hours', 'Opening hours is not found')
		
		try:
			weekday = current_opening_hours.get('weekday_text', 'Weekday schedule not found')
		except:
			weekday = 'N/A'

		rating = resp['result'].get('rating', 'Rating is not found')
		address = resp['result'].get('formatted_address', 'Address is not found')

		geometry = resp['result'].get('geometry', 'Geometry is not found')
		lat = geometry.get('location').get('lat')
		lng = geometry.get('location').get('lng')

		print(resp['result'])
		print(f"Laundry:{name}")
		review_data = []
		
		for review in reviews:
			print(review)
			
			review_data.append({
				'laundry_name': name,
				'icon': icon,
				'icon_background_color': icon_background_color,
				'icon_mask_base_uri': icon_mask_base_uri,
				'international_phone_number': international_phone_number,
				'current_opening_hours': ', '.join(weekday),
				'rating': rating,
				'address': address,
				'latitude': lat,
				'longitude': lng,
				'review_author_name': review.get('author_name', 'N/A'),
				'review_rating': review.get('rating', 'N/A'),
				'review_time': review.get('relative_time_description', 'N/A'),
				'review_timestamp': datetime.fromtimestamp(review.get('time', 'N/A')).strftime('%d/%m/%Y %H:%M:%S'),
				'review_text': review.get('text', 'N/A'),
				'review_original_language': review.get('original_language', 'N/A'),
				'review_author_url': review.get('author_url', 'N/A'),
				'review_author_profile_url': review.get('profile_photo_url', 'N/A'),
			})
	 
		return review_data
	else:
		print('JSON Failed:', resp)
		return [{'place_id': place_id, 'error': 'Review is not found'}]

In [99]:
import openpyxl

# Read excel to get all Laundry Name in Column A
def readColumnA(filename):
    sheet = openpyxl.load_workbook(filename).active

    laundryNames = []
    for cell in sheet['A']:
        laundryNames.append(cell.value)
    return laundryNames

In [100]:
import config

# Change this according the file name
file_name = 'all_laundry.xlsx'
coordinates = readColumnA(file_name)

reviews = []
results = getGeocode(coordinates, config.api_key)

for result in results:
    reviews.append(getPlaceDetails(result['place_id'], config.api_key))

JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Failed: {'results': [], 'status': 'ZERO_RESULTS'}
JSON Faile

In [101]:
import openpyxl

# Check if review data is empty or not and remove if it's empty
reviews = [sublist for sublist in reviews if sublist]

# Export reviews data to excel
if reviews:
    fieldnames = reviews[0][0].keys()
    filename = "exported_reviews.xlsx"

    workbook = openpyxl.Workbook()
    sheet = workbook.active

    for index, fieldname in enumerate(fieldnames, start=1):
        sheet.cell(row=1, column=index, value=fieldname)

    for row, review in enumerate([review for sublist in reviews for review in sublist], start=2):
        for col, fieldname in enumerate(fieldnames, start=1):
            try:
                sheet.cell(row=row, column=col, value=review[fieldname])
            except KeyError:
                print(f"Skipped missing field row: {fieldname}")
                break 

    workbook.save(filename)
    print(f"Reviews data exported to '{filename}' successfully.")
else:
    print("Export Failed! No data exist.")

Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
Skipped missing field row: laundry_name
